In [84]:
import pandas as pd
from tqdm import tqdm
from MeCab import Tagger

kaken = pd.read_csv('kaken/kaken_informatics.csv')

for n,i in tqdm(enumerate(kaken.研究概要.isnull())):
    if i == True:
        kaken = kaken.drop(n)
kaken = kaken.reset_index(drop=True)
kaken = kaken.drop(23)
kaken = kaken.reset_index(drop=True)
kaken = kaken.drop(7108)
kaken = kaken.reset_index(drop=True)
stop_words = []
with open("stop_words.txt") as f:
    for line in f.readlines():
        line = line.rstrip()
        stop_words.append(line)
print(stop_words)

# 形態素解析
# 名詞、動詞、形容詞のみを抽出
import MeCab
tagger = MeCab.Tagger()
texts = []
for sentence in tqdm(kaken.研究概要):
    words = []
    node = tagger.parseToNode(sentence)
    while node:
        features = node.feature.split(",")
        if features[0] in ["名詞","動詞","形容詞"]:
            word = node.surface if features[6] == "*" else features[6]
            if word not in stop_words:
                words.append(word)
                node = node.next
        node = node.next
    texts.append(words)



16271it [00:37, 431.73it/s] 
  3%|▎         | 291/10761 [00:00<00:07, 1418.49it/s]

['', '', '”', '"', '’', "'", ',', ',', '．', '.', '\x08、', '\x08。', '-', '—', '「', '」', '（', '）', '/', '／', '&', '＆', '・', '×', '…', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '０', '１', '２', '３', '４', '５', '６', '７', '８', '９', '一', '二', '三', '四', '五', '六', '七', '八', '九', 'i', 'it', 'm', 'no', 'the', '合う', 'ある', 'いい', 'いう', 'いく', 'いま', '今', 'いる', '駅', 'おく', 'かける', '方', 'がた', '感', '口', 'くる', 'くれる', 'ここ', 'こっち', 'こと', 'こなす', 'こむ', 'これ', 'さ', 'ザ', 'ざす', 'さりげ', '氏', 'ジ', 'しまう', 'しょ', 'しれる', 'する', '性', 'せる', 'そこ', 'そのもの', 'それ', 'それら', 'たち', 'ため', '地', '邸', '邸宅', '的', 'でく', 'とおす', 'とき', 'どこ', 'とまる', 'とる', 'ない', 'なか', 'なす', 'なる', 'なん', '似る', 'の', '分', 'ほう', 'み', 'む', 'もつ', '持つ', 'もの', 'ゆく', 'よい', 'よう', 'らい', 'られる', 'れる', '研究', '手法', '示す', '問題', '結果', '用いる', 'システム', '実現', '構築', '評価', '論文', '調査', '成果', '発表', '提案', '行う', '利用', '開発', '可能', 'モデル', '基づく', 'できる', '情報', '抽出', '検討', '(', ')', '実験', '得る', '明らか', '年度', '方法', ')、', 'and', ':']


100%|██████████| 10761/10761 [00:12<00:00, 857.76it/s]


In [85]:
# gensimをもちいて辞書とコーパスを作成
from gensim import corpora,models
dictionary = corpora.Dictionary(texts)
dictionary.save('kaken.dict') 
corpus = [dictionary.doc2bow(text) for text in texts]


In [135]:
kaken

研究課題名  \
0               多様な認知機能を統合的に扱うための認知特徴空間の同定およびその皮質寄与分布の解明   
1                                            並列索引構造の形式検証   
2                     計算論的アプローチに基づく上肢訓練支援システムと機能回復モデルの構築   
3      Noise-Adaptive Statistical Speech Synthesis in...   
4                ソフトウェア進化促進のためのコンテンツ履歴グラフ構築と管理・分析システムの開発   
5                      ユビキタスコンピューティングにおけるユーザ情報の匿名化に関する研究   
6                   搭乗型道具を活用可能となるヒューマノイドの行動計画・動作知識獲得法の研究   
7                               多腕バンディット問題における最適戦略の構成と発展   
8                                 大規模並列化に適した高精度電子状態理論の開発   
9                             統計的信号処理によるヒューマン・インタフェースの作成   
10                   ロボットの動作から生じるドップラー変化を用いた位置姿勢推定に関する研究   
11                        タッチパネル課題共有場面におけるチンパンジーの行動調整の分析   
12              高度なデータ解析の実現のための機械学習および最適化アルゴリズムの相転移現象の解析   
13              環境モデル徒弟学習の抜本的高速化技術の開発と実用的対話システムのプロトタイプ構築   
14                                 タンパク質・糖鎖の低親和性複合体構造の予測   
15                振動曝露環境下におけるＩＳＯ表面性状パラメータを物理指標とした粗さ感覚の評価   
16                                 １本の毛髪によるストレスの「日輪」の可視化   
17                  視機性動眼反射に潜む非線形力学機構と脳型ロボットビジョン開発に関する研究   
18                 耐タンパデバイスを利用した効率的な関数型暗号設計法および安全性検証法の研究   
19                  逆イジング問題の情報統計力学: エージェント間相互相関の推定とモデリング   
20                  音声コミュニケーションの進化を司る神経基盤の解明～小型霊長類との比較から   
21                 5D世界地図システムによる自然環境・地域文化の国際協働型知識共有環境の実現   
22                               社会的存在としての遠隔操作型アンドロイドの研究   
23                     GPUコアを内蔵するプロセッサによる代数的マルチグリッド法の高速化   
24                不可視に構造化された光による実空間、実物体ベースの新しいメディア表現法の研究   
25                           オカヤドカリの「車体感覚」を伴った道具使用に関する研究   
26                                    同型性判定問題に対する近似手法の研究   
27                       階層ベイズモデルに基づく臨床研究・疫学研究の生物統計手法の開発   
28                        変動感による認知性と受容性を考慮した電気自動車用接近音の設計   
29                           リアルタイム指向ネットワークコンピューティング構成技術   
...                                                  ...   
10731                     再利用向きオブジェクト指向プログラミングシステムに関する研究   
10732  地域計画文書の計算機による知的処理のための知識利用方策に関する基礎研究ー文章の理解と学習のた...   
10733                 幾何演算容易な図形データ構造を援用する大面積画像の高次処理方式の研究   
10734                                 分散型システムの制御方式に関する研究   
10735                           書式に依存しない文字認識システムに関する研究開発   
10736                      属性文法にもとづくソフトウェア自動生成システム講成法の研究   
10737                音声言語によるマン・マシン・インターフェイスの高度化に関する総合的研究   
10738                     図学教育へのコンピュータ・グラフィックスの導入法に関する研究   
10739                      動的知識管理機能を有するデータベースワークベンチの研究開発   
10740                  並列処理計算機の構成方式, 言語及びアルゴリズムに関する総合的研究   
10741             学術情報ネットワークにおける密結合型図書館システムの諸機能の高度化とその応用   
10742                自然言語処理のための標準辞書フォーマットの作成と辞書データベースの構築   
10743                      ベクトル計算機用PASCALの自動ベクトルコンパイラの開発   
10744                  医用病歴画像データベースのための画像検索用ワークステーションの開発   
10745                         ネットワーク接続可能な高性能ワークステーションの開発   
10746                        音声情報による可搬型喉頭癌スクリーニング装置の開発研究   
10747                    数学公式データベースに基づく数式計算エキスパートシステムの研究   
10748                    局所エントロピー・フローに基づく画像情報の感覚的評価関数の研究   
10749                                  知的情報処理における推論機構の研究   
10750            関数的論理型プログラム言語の設計と,それに基づく証明・検証・合成システムの作成   
10751              時空間様相論理に基づくシステム記述言語の設計とその回路自動設計問題への応用   
10752                      日本語処理のためのプログラミング支援環境の構築に関する研究   
10753                              パタン照合アルゴリズムの効率化に関する研究   
10754                                知的分散処理システムの構築に関する研究   
10755                                 自然言語処理における辞書に関する研究   
10756                       あいまいさを含む実システムの評価とモデリングに関する研究   
10757                      HashとSortを用いた並列関係データベースマシンの試作   
10758                         セル構造回路網に基づく手書文字認識システムの試作研究   
10759           Concurrent LISPの基づく多様パラダイム指向プログラミング環境の構築   
10760                        自然言語理解にもとづく日本語文章音声合成システムの研究   

                                              研究課題名 (英文) 研究課題/領域番号  \
0                                                    NaN  25880034   
1                                                    NaN  25880032   
2                                                    NaN  25880031   
3                                                 

In [168]:
time = []
for i,year in enumerate(kaken['研究期間 (年度)']):
    try:
        time.append(int(year[0:4]))
    except:
        pass
time

[2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2013,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,
 2012,

In [131]:
time = []
for year in kaken['研究期間 (年度)']:
    time.append(int(year[0:4]))
from collections import Counter
counter = Counter(time)
time_slice = list(counter.values())
time_slice.reverse()

In [132]:
'''
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
import numpy
from gensim.matutils import hellinger 
ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=dictionary, time_slice=time_slice, num_topics=10)
'''

'\nfrom gensim.models import ldaseqmodel\nfrom gensim.corpora import Dictionary, bleicorpus\nimport numpy\nfrom gensim.matutils import hellinger \nldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=dictionary, time_slice=time_slice, num_topics=10)\n'

In [133]:
from gensim.models.wrappers.dtmmodel import DtmModel
from gensim.corpora import Dictionary, bleicorpus
import pyLDAvis

dtm_path = "/home/makoto/dtm/dtm/dtm"
dtm_model = DtmModel(dtm_path, corpus, time_slice, num_topics=10, id2word=dictionary, initialize_lda=True)
dtm_model.save('dtm_informatics')



In [136]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=0, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [137]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=1, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [138]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=2, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [139]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=3, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [140]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=4, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [141]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=5, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [142]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=6, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [144]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=8, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [145]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=9, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [146]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=10, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [147]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=11, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [148]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=12, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [149]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=13, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [150]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=14, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [151]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=15, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [152]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=16, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [153]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=17, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [154]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=18, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [155]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=19, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [156]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=20, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [157]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=21, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [158]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=22, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [159]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=23, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [160]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=24, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [161]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=25, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [162]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=26, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [163]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=27, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [164]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=28, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)

In [165]:
doc_topic, topic_term, doc_lengths, term_frequency, vocab = dtm_model.dtm_vis(time=29, corpus=corpus)
vis_wrapper = pyLDAvis.prepare(topic_term_dists=topic_term, doc_topic_dists=doc_topic, doc_lengths=doc_lengths, vocab=vocab, term_frequency=term_frequency)
pyLDAvis.display(vis_wrapper)